In [1]:
import pandas as pd
pd.set_option('display.max_rows', 1000)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)
import numpy as np
from numpy import mean
from numpy import std
from numpy import absolute
import scipy
from scipy.optimize import minimize
import time
from sklearn.linear_model import LinearRegression

import matplotlib.pyplot as plt
import warnings

import glob
import random
import pyarrow as pa
import pyarrow.parquet as pq


from pandas import read_csv
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import RepeatedKFold
from sklearn.linear_model import Lasso
from sklearn.preprocessing import StandardScaler

random.seed(10)


# Load up the data and take a look

In [469]:
pq.read_table('/Users/amre/qr_takehome/QR_TAKEHOME_20221012.csv.parquet').to_pandas()


time  sym exch    Q1    Q2        X1       X10      X100      X101  X102      X103      X104      X105      X106  X107      X108      X109       X11      X110      X111  X112      X113       X114       X115       X116      X117       X118      X119       X12       X120      X121       X122      X123       X124      X125       X126      X127      X128      X129       X13       X130      X131      X132      X133       X134      X135      X136      X137       X138      X139       X14       X140      X141      X142      X143      X144      X145      X146          X147      X148          X149       X15      X150          X151      X152          X153      X154          X155      X156          X157      X158      X159       X16      X160      X161      X162      X163      X164      X165      X166      X167      X168      X169       X17       X170       X171      X172      X173       X174       X175       X176       X177       X178       X179  X18       X180       X181      X182  \
0      35101000  SPX  cme  0.15  1.00 -0.713182       NaN -0.527547 -0.756925   NaN       NaN -0.428949  0.417156  0.181037   NaN       NaN -0.620503       NaN -1.146395 -1.345160   NaN       NaN -11.761017 -11.959665        NaN       NaN -42.390644 -4.363106       NaN        NaN       NaN  -6.965027 -4.177066        NaN       NaN  -4.206575 -4.251593       NaN       NaN       NaN  -5.734396 -5.764388       NaN       NaN  -5.853538 -5.873487       NaN       NaN -32.261360 -5.133939       NaN        NaN       NaN -0.228234  0.338036 -0.228234  0.172467  0.000000  0.000000e+00  0.000000  0.000000e+00       NaN  0.000000  0.000000e+00  0.000000  0.000000e+00  0.000000  0.000000e+00  0.000000  0.000000e+00  0.031047  0.004456       NaN  0.014201  0.003080  0.030879  0.022492  0.014123  0.015548  0.029907  0.020783  0.013679  0.014366       NaN   8.553646   8.400100  3.472314  3.275792  52.786850  53.060051  33.249428  33.341400  23.913557  23.794930  NaN  15.133295  14.898062  1.591848   
1      35102000  SPX  cme  0.15  1.00 -0.351432       NaN  0.137588 -0.038695   NaN       NaN  0.648626  1.083001  0.896289   NaN       NaN  0.399210       NaN -0.416161 -0.546562   NaN       NaN -10.352584 -10.489553        NaN       NaN -41.703979 -3.650004       NaN        NaN       NaN  -6.230404 -3.423098        NaN       NaN  -1.858709 -1.885402       NaN       NaN       NaN  -3.467487 -3.528377       NaN       NaN  -3.947181 -3.921672       NaN       NaN -31.530941 -4.412046       NaN        NaN       NaN  0.018255 -0.344887  0.000000 -0.344887  0.000000  0.000000e+00  0.000000  0.000000e+00       NaN  0.000000  0.000000e+00  0.000000  0.000000e+00  0.000000  0.000000e+00  0.000000  0.000000e+00  0.037872  0.062852       NaN  0.017319  0.043440  0.033019  0.036734  0.015100  0.025389  0.030142  0.022206  0.013784  0.015348       NaN   9.687355   9.597380  4.529543  4.613866  54.574039  54.904095  34.605125  34.983704  25.446861  25.386049  NaN  16.325850  16.376923  2.188422   
2      35103000  SPX  cme  0.15  1.00 -0.291459       NaN -0.209708 -0.462202   NaN       NaN  0.273657  0.729117  0.460913   NaN       NaN  0.021654       NaN -0.668896 -0.853899   NaN       NaN  -9.985456 -10.191236        NaN       NaN -42.029278 -4.085559       NaN        NaN       NaN  -6.507039 -3.814589        NaN       NaN  -1.193182 -1.429120       NaN       NaN       NaN  -2.490937 -2.482070       NaN       NaN  -2.489437 -2.480665       NaN       NaN -31.812824 -4.838528       NaN        NaN       NaN  0.000000  0.344887  0.000000  0.344887  0.000000  0.000000e+00  0.000000  0.000000e+00       NaN  0.000000  0.000000e+00  0.000000  0.000000e+00  0.000000  0.000000e+00  0.000000  0.000000e+00  0.013552  0.032788       NaN  0.006197  0.022662  0.026840  0.031984  0.012273  0.022106  0.029546  0.021911  0.013511  0.015144       NaN   9.464967   9.306350  4.226149  4.304823  54.988842  55.238667  34.578438  34.956726  25.606234  25.467007  NaN  16.138180  16.188665  1.210543   
3      3510

***
First, process the data (drop collinear independent variables), and create train and validation datasets using 80/20 split.
***

In [6]:
# Collinear variables were determined using regression in Stata
collinear_vars = ["X10", "X108", "X11", "X113", "X12", "X14", "X146", "X147", "X148", "X149", "X15", "X150", "X151", 
                  "X152", "X153", "X173", "X175", "X177", "X18", "X180", "X184", "X185", "X187", "X19", "X194", 
                  "X197", "X198", "X199", "X201", "X204", "X206", "X211", "X213", "X214", "X216", "X217", "X218", 
                  "X219", "X22", "X220", "X221", "X223", "X228", "X23", "X230", "X233", "X235", "X237", "X238", 
                  "X252", "X253", "X3", "X314", "X32", "X33", "X4", "X49", "X5", "X6", "X68", "X7", "X73", "X82", "X9"
               ]

sparse_vars = ["X114", "X115", "X116", "X117", "X118", "X119", "X120", "X121", "X122", "X123", "X124", "X125", 
               "X126", "X127", "X128", "X129", "X130", "X131", "X132", "X133", "X134", "X135", "X136", "X137", 
               "X138", "X139", "X140", "X141", "X142", "X144", "X145", "X154", "X155", "X156", "X157", "X254", 
               "X255", "X256", "X257", "X258", "X259", "X260", "X261", "X262", "X263", "X264", "X265", "X266"  
              ]

In [468]:
def get_data2(file_name):
    df1 = pq.read_table('/Users/amre/qr_takehome/'+file_name+'.csv.parquet').to_pandas()
    df1['bad_values_count'] = df1.isnull().sum(axis=1)
    df1 = df1[df1['bad_values_count'] ==0]
    df1 = df1.drop(collinear_vars, axis=1)
    df1['date'] = pd.to_datetime(file_name[-8:])
    df1['MONTH'] = df1['date'].dt.month
    df1['WEEK'] = df1['date'].dt.week
    df1 = df1[df1['Q1'] == 1]
    temp = pd.DataFrame((df1 == 0).astype(int).sum(axis=0)).reset_index()
    temp.columns=['var', 'zeros']
    sparse_vars = list(temp.loc[temp['zeros']>0.05*len(df1), 'var'].astype(str))
    df1 = df1.drop(sparse_vars, axis=1)
    df1['time'] = (df1['time'] / 1000) - 35100
    df1['second_hour'] = (df1['time']< 2*60*60).astype(int)
    df1['first_hour'] = (df1['time']< 60*60).astype(int)
    df1['last_hour'] = (df1['time']> 22500 - (60*60)).astype(int)
    return df1


files = glob.glob("/Users/amre/qr_takehome/*.csv.parquet")
train = random.sample(files, int(len(files)*0.8))
validation = [element for element in files if element not in train]

df = pd.DataFrame()
for f in validation:
    temp = get_data2(f[-32:-12])
    df = df.append(temp)


# df = df[~df.isin([999999]).any(axis=1)]

df = df.reset_index()
df.to_csv('/Users/amre/qr_takehome/Desktop/validation.csv')
df

/Users/amre/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:8: FutureWarning: Series.dt.weekofyear and Series.dt.week have been deprecated.  Please use Series.dt.isocalendar().week instead.
  


index     time  sym exch   Q1   Q2        X1      X100      X101      X102      X103      X104      X105      X106      X107      X109      X110      X111      X112       X13      X143      X158      X159       X16      X160      X161      X162      X163      X164      X165      X166      X167      X168      X169       X17       X170       X171       X172       X174       X176       X178       X179       X181      X182      X183      X186      X188      X189      X190      X191          X192      X193       X195       X196        X2       X20       X200       X202       X203       X205       X207       X208       X209       X21      X210      X212      X215       X222      X224       X225      X226      X227      X229      X231       X232      X234      X236      X239       X24      X240      X241      X242      X243      X244      X245      X246      X247      X248      X249       X25       X250      X251       X26       X27       X28       X29       X30       X31  \
0            0      1.0  SPX  cme  1.0  1.0 -0.677949 -3.048911 -2.580594 -2.232045 -2.111436 -1.886198 -2.208954 -1.918247 -2.129777 -2.165094 -2.975729 -2.309892 -2.161043 -0.333275  0.000000 -0.340025 -0.216361 -0.176522 -0.746111 -0.291218 -0.242271 -0.139957 -0.531610 -0.188380 -0.019578 -0.013124 -0.042960 -0.017665 -0.340590 -14.750418 -14.120880 -10.938069 -44.212887 -36.277145 -15.108807 -14.762028 -10.702099 -9.998671 -9.370227 -2.668390 -1.989784 -1.804714 -0.282518 -0.331848 -2.353570e-01 -0.276950 -28.591726 -20.847208  1.331825 -0.057473  -8.731485 -11.695658 -41.272408 -32.616657 -12.268151  -8.052461  -8.639103 -0.559906 -8.034682 -6.107034 -8.160146 -17.033503 -2.141204 -18.445597 -3.126399 -2.498525 -2.110667 -1.943707 -31.931719 -2.848003 -2.776391 -1.342370 -0.001554 -1.486860 -1.139002  5.498759  5.815706  4.226922  4.435130  7.892344  7.835878  5.989035  5.970609 -0.039151 -12.088357 -2.178944 -0.287657 -2.142192 -0.184375 -1.214852 -0.130082 -1.368942   
1            1      2.0  SPX  cme  1.0  1.0 -0.795266  0.245765 -0.243893  0.315638 -0.475915  0.326730  1.088947  0.411801  0.424302  0.042300  0.282660  0.018376  0.343013 -0.401894 -0.658575 -0.069328 -0.053023 -0.258715 -0.106414 -0.071335 -0.120094 -0.071588 -0.184336 -0.096311 -0.014411 -0.008871 -0.022120 -0.011935 -0.368575  -7.315936  -7.598804  -5.811265 -37.274651 -31.543056  -8.105071  -8.684260  -6.825793 -1.020275 -1.302006  1.092159  0.694460  0.609196  0.228385 -0.109822  3.060816e-02  0.052202 -22.562696 -16.100161  1.673202  0.144946  -6.128918  -8.065932 -37.611633 -30.427341  -8.526679  -5.821746  -6.393703  0.014585 -1.916623 -1.739035 -1.924250 -13.381014  0.023132 -16.239069  0.149173 -0.153141 -0.452196  0.401019 -29.363220  0.433297 -0.227005  0.600129  0.046596  0.726945  0.319290  3.031220  2.640980  2.460234  2.381463  2.166552  1.813442  1.797507  1.825598  0.354533  -8.780053  0.160320 -0.113877 -1.007835 -0.117033 -0.841513  0.043739 -0.734406   
2            3      4.0  SPX  cme  1.0  1.0 -1.240632  0.411054  0.149622  0.198094 -0.190832  0.223651  1.194378  0.753569  0.310670  0.153403  0.686881  0.567056  0.200313 -0.266807  0.066484 -0.055548  0.021649 -0.079417 -0.097480  0.029135 -0.125104 -0.052927 -0.219543 -0.071230 -0.019847 -0.009686 -0.034828 -0.013036 -0.337794  -9.375351  -9.486272  -7.756896 -41.045448 -34.850521 -11.609575 -11.973944  -9.548193 -0.526727 -0.663919  0.443774  0.426059  0.314453 -0.394009 -0.415745 -3.202706e-02 -0.107505 -26.053671 -19.365950  1.666475  0.169734  -8.750416 -11.982434 -41.491829 -33.654854 -12.177217  -8.966709  -9.544112  0.332682 -1.697230 -1.759333 -1.693305 -17.231291 -3.220378 -19.452147  0.433926  0.323417  0.639804  0.725473 -29.424623  0.559008 -0.189117  1.035945  0.020058  1.061220  0.880392  2.134599  2.084980  2.072556  1.967177  1.299438  1.280174  1.617657  1.548418  0.030386  -8.635796  0.493576 -0.105975 -1.130256 -0.131386 -1.057309 -0.000599 -1.247604   
3            4      5.0  SPX  cme  1.0  1

# Feature Selection using Lasso

***
Try feature selection using Lasso on one dataset:
***

In [23]:
def get_data(file_name):
    df1 = pq.read_table('/Users/amre/qr_takehome/'+file_name+'.csv.parquet').to_pandas()
    df1['bad_values_count'] = df1.isnull().sum(axis=1)
    df1 = df1[df1['bad_values_count'] ==0]
    df1 = df1.drop(collinear_vars, axis=1)
#     df1['date'] = pd.to_datetime(file_name[-8:])
#     df1['MONTH'] = df1['date'].dt.month
#     df1['WEEK'] = df1['date'].dt.week
    df1 = df1[df1['Q1'] == 1]
    temp = pd.DataFrame((df1 == 0).astype(int).sum(axis=0)).reset_index()
    temp.columns=['var', 'zeros']
    sparse_vars = list(temp.loc[temp['zeros']>0.05*len(df1), 'var'].astype(str))
    df1 = df1.drop(sparse_vars, axis=1)
    df1['time'] = (df1['time'] / 1000) - 35100
#     df1['second_hour'] = (df1['time']< 2*60*60).astype(int)
    df1['first_hour'] = (df1['time']< 60*60).astype(int)
    df1['last_hour'] = (df1['time']> 22500 - (60*60)).astype(int)
    df1.to_csv('/Users/amre/Desktop/'+file_name+'.csv')
    df1 = df1.drop(['time', 'sym', 'exch', 'Q1', 'Q2', 'Y2'], axis=1)
    df1 = df1[list(df1.columns[:-3]) + list(df1.columns[-2:]) + list([df1.columns[-3]])]
    # normalize the features
    X = pd.DataFrame(StandardScaler().fit_transform(df1.drop('Y1', axis=1)), columns=df1.drop('Y1', axis=1).columns).values
    y =  df1.values[:, -1]
    return X, y



In [24]:
X, y = get_data("QR_TAKEHOME_20221012")
model = Lasso(alpha=1.0)
model.fit(X, y)
model.score(X,y)


0.13734335279672405

In [25]:
model.coef_

array([-0.        , -0.        ,  0.        , -0.        , -0.        ,
        0.        ,  0.        ,  0.        , -0.        , -0.        ,
       -0.        , -0.        , -0.        , -0.        ,  0.        ,
       -0.        , -0.        , -0.        , -0.        , -0.        ,
       -0.        , -0.        ,  0.        , -0.        ,  0.        ,
       -0.        , -0.        , -0.        ,  0.        , -0.        ,
       -0.        , -0.        , -0.        , -0.        , -0.        ,
       -0.        , -0.        , -0.        , -0.        ,  0.        ,
       -0.        ,  0.        ,  0.        ,  0.        , -0.        ,
        0.        ,  0.        , -0.        ,  0.        , -0.        ,
       -0.        , -0.        , -0.        , -2.14761352, -0.        ,
       -0.        , -0.        , -0.        , -0.        , -0.        ,
       -0.        ,  0.        , -0.        , -0.        ,  0.        ,
        0.        ,  0.02272174,  0.        ,  0.        ,  0.  

***
Eight features were selected, so I would expect this model to perform well in out-of-sample predictions. However, it performs terribly.
***

In [26]:
X2, y2 = get_data("QR_TAKEHOME_20220107")
model.score(X2,y2)

-0.23768568447167615

***
Run Lasso feature selection on the second dataset, and we see totally different features were selected.
***

In [27]:
X2, y2 = get_data("QR_TAKEHOME_20220107")
model = Lasso(alpha=1.0)
model.fit(X2, y2)
print(model.score(X2,y2))
model.coef_

0.06192169789187052


array([-0.        , -0.        , -0.        , -0.        , -0.        ,
       -0.        ,  0.        ,  0.        , -0.        ,  0.        ,
        0.        ,  0.        ,  0.        , -0.        , -0.        ,
        0.        ,  0.        , -0.        ,  0.        ,  0.        ,
        0.        , -0.        ,  0.        , -0.        ,  0.        ,
       -0.        ,  0.        , -0.        , -0.        , -0.        ,
       -0.        , -0.        ,  0.        ,  0.        , -0.        ,
       -0.        , -0.        , -0.        , -0.        ,  0.        ,
        0.        ,  0.        ,  0.        ,  0.        ,  0.        ,
        0.        ,  0.        ,  0.        , -0.        ,  0.        ,
       -0.        ,  0.        ,  0.        ,  0.        , -0.        ,
       -0.        , -0.        ,  0.        , -0.        , -0.        ,
       -0.        ,  0.        ,  0.        ,  0.        , -0.        ,
        0.        , -0.        , -0.        , -0.        , -0.  

***
I conclude that either we should add Lasso is not appropriate at the moment, I might get back to it when I have a different set of features. 
***

# Feature selection using SelectKBest

***
SelectKBest uses statistical tests to rank the features according to their importance. 

In my case, I use mutual_info_regression because it is more suitable for non-linear regression problems. This scoring function relies on nonparametric methods based on entropy estimation from k-nearest neighbors distances. It is equal to zero if and only if two random variables are independent, and higher values mean higher dependency.
***

In [37]:
def get_data(file_name):
    df1 = pq.read_table('/Users/amre/qr_takehome/'+file_name+'.csv.parquet').to_pandas()
    df1['bad_values_count'] = df1.isnull().sum(axis=1)
    df1 = df1[df1['bad_values_count']==0]
    df1 = df1.drop(collinear_vars, axis=1)
    df1 = df1[df1['Q1'] == 1]
    temp = pd.DataFrame((df1 == 0).astype(int).sum(axis=0)).reset_index()
    temp.columns=['var', 'zeros']
    df1['time'] = (df1['time'] / 1000) - 35100
    df1['first_hour'] = (df1['time']< 60*60).astype(int)
    df1['last_hour'] = (df1['time']> 22500 - (60*60)).astype(int)
    df1 = df1.drop(['time', 'sym', 'exch', 'Q1', 'Q2', 'Y2', 'bad_values_count'], axis=1)
    df1 = df1[list(df1.columns[:-3]) + list(df1.columns[-2:]) + list([df1.columns[-3]])]
    data = df1.values
    X, y = data[:, :-1], data[:, -1]
    return X, y, df1.columns[:-1]



In [38]:
from sklearn.feature_selection import SelectKBest, mutual_info_regression, f_regression
selector = SelectKBest(score_func=f_regression, k=25)

files = glob.glob("/Users/amre/qr_takehome/*.csv.parquet")

df_scores = pd.DataFrame()
for f in files:
    X, y, cols = get_data(f[-32:-12])
    selector.fit(X, y)
    new_row = pd.Series(selector.scores_, index=cols)
    df_scores = df_scores.append(new_row, ignore_index=True)
    print(f)


/Users/amre/qr_takehome/QR_TAKEHOME_20221012.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220119.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220712.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220923.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220505.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20230224.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20221205.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220831.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20221219.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220720.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20221020.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20230113.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220519.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220425.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220803.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20230216.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220105.csv.parquet
/Users/amre/qr_takehome/QR_TAKE

/Users/amre/qr_takehome/QR_TAKEHOME_20230209.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20221011.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220711.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20221103.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20221228.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220323.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20221118.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220421.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220915.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220829.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220316.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20230117.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20221024.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220204.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220218.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20221201.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220413.csv.parquet
/Users/amre/qr_takehome/QR_TAKE

/Users/amre/qr_takehome/QR_TAKEHOME_20220727.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220315.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220207.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20221027.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20230303.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20221230.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220422.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220804.csv.parquet
/Users/amre/qr_takehome/QR_TAKEHOME_20220916.csv.parquet


In [14]:
df_scores

X1      X100      X101      X102      X103      X104      X105      X106      X107      X109      X110      X111      X112      X114      X115      X116      X117      X118      X119      X120      X121      X122      X123      X124      X125      X126      X127      X128      X129       X13      X130      X131      X132      X133      X134      X135      X136      X137      X138      X139      X140      X141      X142      X143      X144      X145      X154      X155      X156      X157      X158      X159       X16      X160      X161      X162      X163      X164      X165      X166      X167      X168      X169       X17      X170      X171      X172      X174      X176      X178      X179      X181      X182      X183      X186      X188      X189      X190      X191      X192      X193      X195      X196        X2       X20      X200      X202      X203      X205      X207      X208      X209       X21      X210      X212      X215      X222      X224      X225  \
0    0.024273  0.018099  0.007765  0.010788  0.003386  0.015337  0.021081  0.016636  0.027331  0.013574  0.013074  0.009840  0.004290  0.049992  0.045088  0.059811  0.056084  0.228526  0.178969  0.295871  0.269842  0.118850  0.108554  0.171895  0.181733  0.011300  0.005221  0.014319  0.012364  0.011208  0.015029  0.010594  0.009702  0.008567  0.008730  0.017249  0.007582  0.008630  0.179499  0.150813  0.268885  0.266175  0.430075  1.979537  0.605398  1.640448  0.018701  0.393342  0.050679  0.793320  0.000169  0.010399  0.018849  0.000440  0.012850  0.028467  0.035097  0.025518  0.035546  0.135718  0.137041  0.120044  0.138405  0.009435  0.044649  0.037642  0.023344  0.293197  0.697088  0.105408  0.111823  0.122817  0.007799  0.010246  0.000000  0.051266  0.011505  0.000000  0.026298  0.054500  0.022801  0.279720  0.473105  0.033766  0.007620  0.068433  0.350602  0.351959  0.344042  0.134293  0.173705  0.172478  0.009474  0.000000  0.004673  0.003698  0.295908  0.307106  0.298681   
1    0.037353  0.008787  0.000000  0.000000  0.008564  0.014638  0.020035  0.015821  0.030636  0.009205  0.002194  0.000000  0.016523  0.030646  0.030296  0.036551  0.035057  0.119819  0.116468  0.213135  0.140497  0.064455  0.064520  0.072232  0.061892  0.000000  0.007307  0.005664  0.000357  0.016076  0.020284  0.004528  0.012103  0.010559  0.016260  0.000000  0.001496  0.003908  0.086885  0.087744  0.122258  0.134264  0.448786  2.121640  0.781438  1.715830  0.009752  0.325384  0.005794  0.806242  0.000000  0.002361  0.040933  0.000000  0.008626  0.025572  0.020845  0.023489  0.033241  0.109565  0.127698  0.073414  0.136892  0.009902  0.025305  0.016479  0.037942  0.343653  0.709356  0.095366  0.105784  0.115140  0.000000  0.000000  0.001492  0.019233  0.002288  0.007983  0.012146  0.034704  0.018745  0.237731  0.495030  0.038354  0.000000  0.041052  0.443166  0.434601  0.442866  0.142879  0.146622  0.148741  0.016649  0.015011  0.001170  0.005410  0.284860  0.294760  0.290866   
2    0.036272  0.015283  0.016089  0.012758  0.025104  0.019875  0.014247  0.021782  0.025083  0.009395  0.004780  0.013214  0.009462  0.032914  0.033863  0.040217  0.043642  0.114433  0.076479  0.116749  0.129164  0.066159  0.058970  0.068746  0.072292  0.008411  0.000380  0.008342  0.004546  0.008026  0.028610  0.031219  0.026431  0.028747  0.018386  0.012847  0.019109  0.017116  0.087216  0.078522  0.078468  0.082366  0.500702  1.920879  0.793048  1.474071  0.032950  0.627824  0.033041  1.056031  0.007093  0.000000  0.024886  0.000500  0.001185  0.020533  0.021680  0.016554  0.023834  0.126849  0.152014  0.089448  0.147919  0.009991  0.062280  0.059906  0.055411  0.477991  0.997593  0.146146  0.148896  0.157887  0.019154  0.013711  0.006990  0.053668  0.008817  0.021678  0.025657  0.078528  0.047760  0.341537  0.593626  0.033332  0.004207  0.062489  0.543202  0.547507  0.551111  0.184254  0.179964  0.175607  0.016139  0.014043  0.010249  0.018579  0.360208  0.356728  0.353127   
3    0.027742  0.016382

In [18]:
pd.DataFrame(df_scores.sum()).reset_index().sort_values(0)

index           0
198        X326    0.823007
197        X325    0.898462
131        X263    0.901146
130        X262    0.935325
226        X352    0.960406
164        X293    0.963798
225        X351    0.980519
163        X292    1.028845
118         X25    1.041121
257         X43    1.211922
84          X20    1.284433
223         X35    1.299181
107         X24    1.468393
250        X374    1.554712
212         X34    1.615296
53         X160    1.615368
50         X158    1.666682
25         X126    1.670248
26         X127    1.687197
51         X159    1.714288
28         X129    1.886836
242        X367    1.926929
180        X308    1.948605
171         X30    1.992864
298         X87    2.021024
243        X368    2.021421
181        X309    2.032368
150        X280    2.103992
297         X86    2.238090
211        X339    2.238621
108        X240    2.271570
154        X284    2.272436
205        X333    2.293179
151        X281    2.321603
299         X88    2.344727
296         X85    2.359067
106        X239    2.367172
295         X84    2.377582
127         X26    2.396604
139        X270    2.409453
216        X343    2.463746
213        X340    2.486478
167        X296    2.513464
63          X17    2.552014
109        X241    2.555636
155        X285    2.591782
206        X334    2.639235
54         X161    2.653154
217        X344    2.704037
229        X355    2.711656
172        X300    2.731471
140        X271    2.739663
260         X46    2.764322
168        X297    2.828640
12         X112    2.859176
123        X256    2.908756
165        X294    2.909959
234         X36    2.913355
183        X310    2.924008
9          X109    2.928060
152        X282    2.935720
233        X359    2.970349
191        X319    2.994757
230        X356    3.005033
166        X295    3.006030
74         X186    3.012515
228        X354    3.068612
227        X353    3.074807
173        X301    3.092770
184        X311    3.106704
174        X302    3.111596
11         X111    3.118482
153        X283    3.148835
156        X286    3.150418
169        X298    3.151244
10         X110    3.221169
244        X369    3.322919
158        X288    3.333143
125        X258    3.352048
192        X320    3.366060
157        X287    3.373447
124        X257    3.379420
193        X321    3.380203
235        X360    3.404243
246        X370    3.454995
262         X48    3.461626
132        X264    3.470993
175        X303    3.495505
161        X290    3.516907
170        X299    3.531592
27         X128    3.549525
272         X59    3.565708
275         X62    3.571147
214        X341    3.591225
187        X315    3.613069
199        X327    3.636497
72         X182    3.644694
274         X61    3.684147
220        X347    3.695375
218        X345    3.738375
215        X342    3.771297
159        X289    3.779967
73         X183    3.785384
231        X357    3.810195
126        X259    3.868856
273         X60    3.896220
134        X266    3.907319
112        X244    3.926816
194        X322    3.943649
162        X291    3.944393
219        X346    3.969794
236        X361    3.985583
111        X243    3.998530
276         X63    3.999093
282         X70    4.014775
283         X71    4.042520
113        X245    4.073050
281         X69    4.091643
232        X358    4.101153
133        X265    4.125357
302         X91    4.202551
29          X13    4.251770
221        X348    4.286912
201        X329    4.307166
284         X72    4.308583
110        X242    4.310439
117        X249    4.313783
115        X247    4.330473
200        X328    4.353134
237        X362    4.362111
100        X227    4.368502
95         X215    4.377713
300         X89    4.383605
116        X248    4.409163
114        X246    4.447352
222        X349    4.466916
303         X92    4.493334
128        X260    4.501178
178        X306    4.506857
35         X135    4.558452
304         X93    4.570832
37         X137    4.582994
135   

# Neural Networks

In [28]:
import torch
import torch.nn as nn
import torch.nn.functional as F

In [29]:
X, y = get_data('QR_TAKEHOME_20221012')
X_train_tensor = torch.from_numpy(X).float()
y_train_tensor = torch.from_numpy(y).float()

X2, y2 = get_data('QR_TAKEHOME_20220119')
X_test_tensor = torch.from_numpy(X2).float()
y_test_tensor = torch.from_numpy(y2).float()


***
Try a hidden layer with 24 neuron and ReLU activation:
***

In [31]:
# Initialize the parameters to be random draws
W00 = torch.randn(159, 24)
W01 = torch.randn(24, 1)
b00 = torch.randn(1, 24)
b01 = torch.randn(1, 1)

# Shrink the parameters
W00 = (W00-0.5)*(1/(159**0.5))
W01 = (W01-0.5)*(1/(24**0.5))
b00 = (b00-0.5)*(1/(24**0.5))
b01 = (b01-0.5)*(1/(1**0.5))

W00.requires_grad = True
W01.requires_grad = True
b00.requires_grad = True
b01.requires_grad = True

epochs = 1000
loss_list_a = ()

learning_rate = 1e-2
optimizer = torch.optim.Adam((W00,W01,b00,b01), lr=learning_rate)
# optimizer = torch.optim.SGD((W00,W01,b00,b01), lr=learning_rate, weight_decay=1e-5)  # L1 regularization

for epoch in range(epochs):
    optimizer.zero_grad()
    y_hat = ((X_train_tensor.mm(W00) + b00).clamp(min=0)).mm(W01) + b01
    loss = torch.nn.MSELoss()
    output = loss(y_hat, torch.reshape(y_train_tensor, y_hat.shape)) 
    output.backward()
#     print(output)
    optimizer.step()
    

In [35]:
r2_score(torch.reshape(y_train_tensor, y_hat.shape).detach().numpy(), y_hat.detach().numpy())


0.9589108013036622

***
As you can see above, Neural Networks can fit the prediction model pretty well, but again the out-of-sample prediction is pretty poor. 
***

In [34]:
from sklearn.metrics import r2_score
y_hat_test = ((X_test_tensor.mm(W00) + b00).clamp(min=0)).mm(W01) + b01
r2_score(torch.reshape(y_test_tensor, y_hat_test.shape).detach().numpy(), y_hat_test.detach().numpy())


-6.949460361111446